In [1]:
using Plots
using DelimitedFiles
using DifferentialEquations
using Interpolations
using BenchmarkTools

In [2]:
const neqs = 14
const Vtemp = 13. # kT/Ze : temperature equivalent voltage for Ca ions (2+) - mV */

13.0

In [3]:
path_to_stim_file = "datafiles/N2_stim.txt"

"datafiles/N2_stim.txt"

In [4]:
stim_values = readdlm(path_to_stim_file, Float64)
stim = LinearInterpolation(stim_values[:, 1], stim_values[:, 2])
Iapp(t)::Float64 = stim(t)

Iapp (generic function with 1 method)

In [5]:
# lower = [0.3, 70.,  0.,  40., 0.,   0.,  0.,  0.,  -95., 0.01, -120., 0.0, 0.0,  0.03, 0.01, 0.05]
# upper = [0.4, 130., 20., 54., 130., 80., 80., 12., -60., 0.6,  -40.,  10., 10.,  0.37, 100., 0.3]

# Vlow = -100.*ones(11)
# Vup  = zeros(11); Vup[9] = 40

# dVlow = [5., -60., 5.0, 5.0, -60.0, 5.0, 5., -60., 5., 5., -60.]
# dVup  = [100., -10., 100.0, 100., -10.0, 100., 100., -10., 100., 100., -10.]

# dVtlow = [+1.0, 1.0, 1.0, 1.0, -1.0, 1.0, 5.0,  5.0, 5.0, 5.0, 5.0]
# dVtup  = [+50., 50., 50., 50., -50., 50., 100., 50., 50., 50., 50.]

# t0low = [0.02, 0.02, 0.02, 0.02, 1.0,  0.02, 0.02, 0.02, 0.02, 0.02, 0.02]
# t0up  = [0.7,  0.7,  0.7,  0.7,  200., 0.07, 10.0, 150., 0.7,  20.,  25.]

# τϵlow = [0.001, 0.001, 0.001, 0.001, 1.0,  1.0,  1.0,  1.0,  1.0,  1.0,  1.0];
# τϵup  = [0.1,   1.0,   1.0,   1.0,   500., 100., 100., 100., 100., 100., 5000.];

# delta_avlow = [0.0,   0.0,  0.0]
# delta_avup  = [2000., 10.0, 50.]

In [6]:
# Ccap = 0.3 #Capacitance of the nerve fibre - uF/cm^2 */
# gNa = 120. # Sodium conductance - mS/cm^2 */
# gNaP = 0. # Persistent sodium conductance - mS/cm^2 */
# ENa = 50. # Sodium action potential - mV */
# gA1 = 0.7865198 # Potassium conductance of A1 channel - mS/cm^2 */
# gA2 = 1.138630 #  Potassium conductance of A2 channel - mS/cm^2 */
# gK2 = 0. # Potassium conductance of K2 channel - mS/cm^2 */
# gC = 0. # Calcium activated potassium current - mS/cm^2 */
# EK = -90. # Potassium action potential - mV */
# gL = 0.01970969 # Leakage conductance - mS/cm^2 */
# EL = -84.18847 # Leakage action potential - mV */
# gou = 0.01164139 # Conductivity of inward Ca current (outward ions coming in) - mS/cm^2 */
# gin = 1e-4 # Conductivity of outward Ca current (inward ions coming out) - mS/cm^2 */
# gh = 0.1 # Conductivity of h current ~ 0.03 - 0.37ms/cm2 */
# rlt = 5.758333 # ratio between the L and T current conductivity */
# Iarea = 0.151255 # Surface area of injected current - x10^{-3}cm^2 */

# # # Threshold of gate variable - mV ; i=1...12
# V = [-27.682, -75.5238, -60.997, -65.12, -74.9259, -51.4117, -80., -80.55488, 7., -56.03685, -75.]
# # # Voltage width of gate sigmoid - mV ; i=1...12 
# dV = [ +27.470, -23.8346, +25., +39.8276, -25.6701, +23.8666, +29., -5., 26., 23.78036, -10.]

# dVt = [+5., 5., +33.095, +5., -5., +15.3232, +57., 21.83786, 36., 31.79630, 20.]
# # # Asymptotic value of tau - ms ; i=1...12 */
# t0 = [0.05118, 0.431129, 0.2666 , 0.417067, 156.7156, 0.09, 0.9, 52.836, 0.1, 4.086303, 5]
# # # Width of tau function - ms ; i=1...12 */
# τϵ = [0.0120 , 0.105836, 0.06917, 0.5, 210, 29, 34.857, 64.2225, 6.4, 22.53280, 1000];

# p = [Ccap,gNa,gNaP,ENa,gA1,gA2,gK2,gC,EK,gL,EL,gou,gin,gh,Iarea,rlt, V..., dV..., dVt..., t0..., τϵ..., 0.0, 0.790126, 5.];
# θ =  [-60.03044592275348, 0.08305051640996845, 0.5918820125394436, 0.032502774912230074, 0.9578577736901883, 0.04629529548544211, 0.1675458523007507, 0.06815189950067448, 0.09895678173358906, 0.2003161027660228, 0.7115347072627934, 0.9971046249079425, 0.6582655111851267, 0.7738910314659763, 0.37403393323286555, 128.7125227679851, 3.925093829794128, 40.60251287161679, 64.14212008853946, 4.085067971208834, 2.268414575279405, 0.9514461544647169, -68.2418546160535, 0.13308287441542851, -82.40881670953456, 2.8619409224298624, 3.2865709173213964, 0.2895222220871655, 0.10684980590621901, 2.485005626815731, -0.2610237585670916, -10.742950780708355, -4.7530098146850435, -20.27566204176513, -97.3512696327712, -0.3013152008829678, -13.839895998185526, -32.75937772286731, 39.50938475935925, -20.43755093308482, -95.95201212448666, 19.690295874743235, -10.061640021377151, 5.018312848123933, 46.35845677704906, -11.465981758511944, 13.087683601605352, 44.91768060943197, -28.23981471786049, 39.682665219133305, 10.195079366843393, -50.7820666625916, 14.280138172456926, 4.81929837187022, 9.157953243504348, 24.132618208419498, -40.68443776612459, 47.85059217227679, 99.21390311447914, 32.36151060026927, 17.21139677770007, 7.412800946071803, 13.024026920750519, 0.021079535334036316, 0.11775571257450962, 0.1736662154446968, 0.35456539197699743, 68.16362760178238, 0.5686994765004793, 1.3823333525736219, 131.45402162035006, 0.025149146603503758, 0.7274220789506627, 2.8855462370111296, 0.07509428779616947, 0.6259117113684444, 0.18477840159008044, 0.0012061077999847235, 168.65001844490962, 2.2348869547461847, 1.085183248067053, 75.35123886928726, 2.6165872514534434, 48.38131869945162, 2599.227461043693, 1947.2733522335632, 5.299747491546443, 49.39468787002162];

# θ = [-60.28878256985282, 0.05554587272961692, 0.16137123634783393, 0.24817523371333938, 0.8562206381613802, 0.2616959976445733, 0.4523900147137674, 0.09783486455534038, 0.25974479063171213, 0.03893727712688822, 0.0273467886395152, 0.6591927774474613, 0.01424620263290174, 0.29259190711255395, 0.39101527703583594, 87.37118064795209, 5.284410784614515, 44.18155985246461, 127.26389571995023, 26.460573532390715, 1.687164641262303, 9.6905767426841, -60.39489181241656, 0.015536535581746419, -103.67825822424837, 0.5020220259783582, 5.618557097261795, 0.21801523917914353, 0.26067985771286944, 0.7190594778342785, -2.665432101270909, -4.924730718565542, -10.75667531411014, -6.241447416771948, -16.34284236786752, -5.2116598118048785, -17.004687524938674, -88.72434145768456, 29.801242515453225, -5.572171217557127, -80.01081192671326, 30.564348452276597, -29.176907030675, 5.093841474475086, 21.72639994217304, -11.913912352130843, 22.44548559292793, 11.563638690063517, -59.22167952270222, 12.216041156187794, 45.5987490161164, -18.159972464844536, 8.44399282708238, 28.400053096467026, 21.296064184759967, 21.886422934012774, -39.423151113142836, 49.88267819336243, 86.66454092049304, 6.555471842723962, 29.733217922278584, 7.83904666072771, 6.250702186226046, 0.04698586157323167, 0.0723871572388891, 0.32901105936842645, 0.6248777951164554, 69.10333939025973, 0.08531219933694154, 7.895732183780274, 135.2525181499104, 0.47922657765897486, 0.021309419002814443, 16.05126575053637, 0.06287760570635312, 0.92838929636234, 0.0021149560553826207, 0.6164560884327119, 423.88596522058623, 16.59888178487136, 96.88259406199128, 65.24962402240027, 8.693737083581745, 62.76115527694126, 1762.6525093267828, 1969.5858681148889, 2.019482660937158, 49.659290726681306];
θ=[-61.93402836804239, 0.053999984513550134, 0.8677675132377433, 0.21094758823620002, 0.8673893800823501, 0.06463106009370051, 0.5368278680702148, 0.034801309766394395, 0.2629320245028402, 0.18635713309843333, 0.992863241496597, 0.9879736378591375, 0.5639252977789222, 0.7703557770831406, 0.3999940134854983, 150.65112731743588, 8.925651590974955, 49.086890011293676, 124.46183364682842, 0.7326262126952293, 1.5787349674992859, 3.7808472023523008, -66.22008947137167, 0.012024239193339614, -105.61790029997763, 0.6471293077332771, 8.08863953487089, 0.20724216148907304, 0.2728691459839464, 14.531212521513075, -0.054064741667474436, -22.78305852040714, -0.7153235615665068, -15.533841412033809, -86.08017380269727, -8.534653707506266, -0.11176514742260224, -43.4579767881865, 28.690779089823195, -0.00012204864425768847, -99.99664591194461, 31.775823913365354, -24.78067041995729, 6.005340205277638, 8.63823861520788, -10.087948987067847, 10.862059490607107, 33.81870582735651, -22.094680223135065, 10.147666479022288, 55.10854255397067, -28.051128176925005, 8.291500889922348, 25.575861938775848, 13.759408712422493, 11.388013273642223, -46.93101265686462, 16.32587595005947, 93.31552392777911, 37.665821487984786, 29.67668073324702, 9.580115826685166, 20.18556370676597, 0.02354327054488278, 0.19755436289318964, 0.14056010764790958, 0.6789422014322583, 176.39691337734806, 0.020257220783194835, 1.2471745968859276, 53.28620013766909, 0.16081583040084538, 0.030454186084830095, 1.8974888113214765, 0.06494438535366333, 0.5733558157973574, 0.5682582149312141, 0.1481098706558182, 103.43239161540912, 7.265638983689308, 4.057076960728887, 79.23928255912374, 33.06275563454173, 42.99153018700545, 197.689392415391, 914.1897391966728, 3.2050352920928056, 46.321464493541086];

In [7]:
function albeta(VV, V, dV, dVt, aV4, t0, τϵ, delta)
# calculation of alpha and beta variable given the membrane voltage VV */
#    int j;
#    double thetai,thetait,tauj,thetai2,thetai1;
    alpha = zeros(14)
    beta = zeros(14)
    for j in 2:neqs
        thetai = (VV-V[j])/dV[j];
        thetait = (VV-V[j])/dVt[j];
        if j==6 || j==8 # A2 and K2 tau_h */
            tauj = t0[j]+delta[j]+0.5*(1-tanh(1000*(VV-V[j]-aV4[j])))*(τϵ[j]*(1-tanh(thetait)*tanh(thetait))-delta[j]);
        else
            if (j == 11) #T tau_h */
                thetai2 = (VV-V[j])/dVt[j]
                thetai1 = (VV-V[j])/aV4[j]
                tauj = t0[j]+τϵ[j]*(1+tanh(thetai2))*(1-tanh(thetai1))*(1-tanh(1000*(VV-V[j]))*tanh(thetai2+thetai1))/(1+tanh(thetai2)^2)
            else
                tauj = t0[j]+τϵ[j]*(1 - tanh(thetait)*tanh(thetait));
            end
        end
        alpha[j] = 0.5*(1+tanh(thetai))/tauj
        beta[j] = 0.5*(1-tanh(thetai))/tauj
    end
    return alpha, beta
end

function Nogaret_N2(dyydx::Array{Float64, 1}, yy::Array{Float64, 1}, p::Array{Float64, 1}, t::Float64)
    Ccap,gNa,gNaP,ENa,gA1,gA2,gK2,gC,EK,gL,EL,gou,gin,gh,Iarea,rlt = @view p[1:16]
    
    V1, V7, V8 = 0.0, -43., -59.
    V2, V3, V4, V5, V6, V9, V10, V11, V12, V13, V14 = @view p[17:27]
    V = [V1, V2, V3, V4, V5, V6, V7, V8, V9, V10, V11, V12, V13, V14]
    
    dV1, dV7, dV8 = 0.0, +34., -21.
    dV2, dV3, dV4, dV5, dV6, dV9, dV10, dV11, dV12, dV13, dV14 = @view p[28:38]
    dV = [dV1, dV2, dV3, dV4, dV5, dV6, dV7, dV8, dV9, dV10, dV11, dV12, dV13, dV14]
    
    dVt1, dVt7, dVt8 = 0.0, +32., +25.
    dVt2, dVt3, dVt4, dVt5, dVt6, dVt9, dVt10, dVt11, dVt12, dVt13, dVt14 = @view p[39:49]
    dVt = [dVt1, dVt2, dVt3, dVt4, dVt5, dVt6, dVt7, dVt8, dVt9, dVt10, dVt11, dVt12, dVt13, dVt14]
    
    t01, t07, t08 = 0.0, 9.9, 50.
    t02, t03, t04, t05, t06, t09, t010, t011, t012, t013, t014 = @view p[50:60]
    t0 = [t01, t02, t03, t04, t05, t06, t07, t08, t09, t010, t011, t012, t013, t014]
    
    τϵ1, τϵ7, τϵ8 = 0.0,  66., 530.
    τϵ2, τϵ3, τϵ4, τϵ5,  τϵ6, τϵ9, τϵ10, τϵ11,τϵ12, τϵ13, τϵ14 = @view p[61:71]
    τϵ = [τϵ1, τϵ2, τϵ3, τϵ4, τϵ5, τϵ6, τϵ7, τϵ8, τϵ9, τϵ10, τϵ11,τϵ12, τϵ13, τϵ14]
    
    delta = Float64[0, 0, 0, 0, 0, 0, 0, 450., 0, 0, 10., 0, 0, 0]
    aV4 = Float64[0, 0, 0, 0, 0, 0.790126, 0, 0, 0, 0, 5, 0, 0, 0]
    
    delta[6] = p[72]
    aV4[6], aV4[11] = p[73], p[74]
    
    alpha, beta = albeta(yy[1], V, dV, dVt, aV4, t0, τϵ, delta)
    
    yy1 = yy[1]/Vtemp;
    yy2 = 1+yy1/51 #Computes the (exp(x)-1)/x function to avoid divergence */
    for k in 50:-1:2
        yy2 = 1. + (yy1/k)*yy2
    end

    dyydx[1] = (gNa*yy[2]^3*yy[3]+gNaP*yy[4])*(ENa-yy[1]);
    dyydx[1] += (gA1*yy[13]^4+gA2*yy[5]^4*yy[6]+gK2*yy[7]^4*yy[8]+gC*yy[12])*(EK-yy[1]);
    dyydx[1] += (rlt*yy[9]^2+yy[10]^2*yy[11])*Vtemp*(gou-gin*exp(yy1))/yy2;
    dyydx[1] += gL*(EL-yy[1])+gh*yy[14]*(-43-yy[1])+(Iapp(t)-yy[1]/1550)/Iarea #was yy[0]/2260
    dyydx[1] /= Ccap;
    for k in 2:neqs 
        dyydx[k] = alpha[k]*(1-yy[k])-beta[k]*yy[k] 
    end
end

Nogaret_N2 (generic function with 1 method)

In [19]:
function load_data(file_name, n_start, n_end; plot_data=false)
    input_data = readdlm(file_name, Float64)
    if n_start == 0
        n_start+=1
        num_pts+=1
    end
    time = input_data[n_start:n_end, 1]
    data = input_data[n_start:n_end, 2:end]

    if plot_data
        num_plots = size(data)[2]
        p = plot(time, data, layout = (1, num_plots), legend = false)
        display(p)
    end
    return time, data
end

load_data (generic function with 1 method)

In [13]:
ys = θ[1:14]
tstart = 1200. * 0.02
tend = 1400

1400

In [14]:
prob = ODEProblem(Nogaret_N2, ys, (tstart, tend), θ[neqs+1:end]);

In [37]:
sol = solve(prob, Vern9(), abstol=1e-10, reltol=1e-10);

In [38]:
length(data_t)

83801

In [44]:
path_to_obs = "datafiles/N2_volt.txt"
nstart = Int(tstart/0.02)
nend = Int(tend/0.02)
data_t, data_u = load_data(path_to_obs, nstart, nend)
plots = plot(data_t, data_u,
             label = "Data", layout = (2, 1), legend=false, c="black")
plot!(plots[2], sol.t, Iapp.(sol.t), c="blue", alpha=0.5)
ylabel!(plots[1], "Voltage (mV)")
ylabel!(plots[2], "Stimulus (nA)")
xlabel!(plots[2], "Time (ms)")
title!(plots[1], "HVCX Data")
# savefig(plots, "X_proj_neuron_data.pdf")

In [47]:
gr(size=(700,400), xtickfontsize=10, ytickfontsize=10, xguidefontsize=12, yguidefontsize=12, legendfontsize=5, dpi=300, grid=(:y, :gray, :solid, 1, 0.4), foreground_color_legend = nothing, background_color_legend = nothing);

path_to_obs = "datafiles/N2_volt.txt"
# data_t, data_u = load_data(path_to_obs, 1200, 85000)
plot(data_t, data_u, label = "Data", c = "black")
plot!(sol, vars = (1), lw = 1.6, alpha = 0.7,
      label = "Est/Pred",legend=:bottomleft, c = "red")

# plot!(plots[2], sol.t, Iapp.(sol.t), c="red", legend=false)

vline!([46200*0.02], lw = 2, c = "black", ls=:dash, label = "Estim/Pred boundary")
# vline!(plots[2], [46200*0.02], lw = 2, c = "black", ls=:dash)
title!("Prediction Window")
ylabel!("Voltage (mV)")
# ylabel!(plots[2], "Stimulus (nA)")
xlabel!("Time (ms)")
# xlims!(plots[2], data_t[1], data_t[end])

xlims!(900, 1400)
savefig("X_proj_neuron_pred.pdf")

In [117]:
600/0.02

30000.0

In [46]:
@benchmark solve($prob, Tsit5(),save_everystep=false)

BenchmarkTools.Trial: 207 samples with 1 evaluation.
 Range (min … max):  15.010 ms … 37.670 ms  ┊ GC (min … max): 0.00% … 26.50%
 Time  (median):     24.597 ms              ┊ GC (median):    0.00%
 Time  (mean ± σ):   24.143 ms ±  5.175 ms  ┊ GC (mean ± σ):  4.24% ±  9.05%

  ▁                        ▇█                                  
  █▄▄▃▃▄▅▇▃▃▁▄▃▃▃▃▃▃▃▃▃▃▄▄███▃▅▁▃▄▄██▇▄▃▁▃▁▃▁▃▃▁▁▃▁▁▁▃▃▁▃▄▃▁▃ ▃
  15 ms           Histogram: frequency by time        37.2 ms <

 Memory estimate: 12.37 MiB, allocs estimate: 81057.

In [19]:
dyydx = zeros(14)
@benchmark Nogaret_N2($dyydx, $ys, $p, 0.0)

BenchmarkTools.Trial: 10000 samples with 10 evaluations.
 Range (min … max):  1.870 μs …  1.145 ms  ┊ GC (min … max): 0.00% … 99.34%
 Time  (median):     2.160 μs              ┊ GC (median):    0.00%
 Time  (mean ± σ):   2.482 μs ± 11.447 μs  ┊ GC (mean ± σ):  4.58% ±  0.99%

  ██▃  ▄▇▆▅▅▃▂                  ▂▂▁     ▄▃▃▃▂▁▁              ▂
  ███▇▅█████████▇███▇▇▅▆▆▅▄▅▆▇▇▆███▆▇▇▆████████▇█▇▆▆▄▅▅▄▃▃▃▃ █
  1.87 μs      Histogram: log(frequency) by time     4.49 μs <

 Memory estimate: 1.72 KiB, allocs estimate: 11.

In [15]:
@profile Nogaret_N2(dyydx, ys, p, 0.0)

In [20]:
Profile.print()

Overhead ╎ [+additional indent] Count File:Line; Function
  ╎4  @Base/task.jl:356; (::IJulia.var"#15#18")()
  ╎ 4  @IJulia/src/eventloop.jl:8; eventloop(::ZMQ.Socket)
  ╎  4  @Base/essentials.jl:709; invokelatest
  ╎   4  @Base/essentials.jl:710; #invokelatest#1
  ╎    4  ...c/execute_request.jl:67; execute_request(::ZMQ.Socket, :...
  ╎     4  .../SoftGlobalScope.jl:65; softscope_include_string(::Modu...
 4╎    ╎ 4  @Base/loading.jl:1091; include_string(::Function, ::...
  ╎28 @Base/task.jl:442; task_done_hook(::Task)
  ╎ 28 @Base/task.jl:712; wait
27╎  28 @Base/task.jl:704; poptask(::Base.InvasiveLinkedLis...
Total snapshots: 36
